In [106]:
from pymongo import MongoClient
import pandas as pd
import pandas
from itertools import chain
import numpy as np

import pickle

In [95]:

from bson import json_util, ObjectId
from pandas.io.json import json_normalize
import json

def mongo_to_dataframe(mongo_data):

        sanitized = json.loads(json_util.dumps(mongo_data))
        normalized = json_normalize(sanitized)
        df = pd.DataFrame(normalized)

        return df

In [96]:
client = MongoClient()
client.list_database_names()

['admin', 'books', 'comedy_covid', 'config', 'local', 'outings']

In [97]:
db = client.comedy_covid
db.list_collection_names()

['covid_comedy_youtube_stats',
 'covid_comedy_youtube_transcripts2',
 'covid_comedy_youtube_comments_test',
 'covid_comedy_youtube_comments',
 'covid_comedy_youtube_transcripts']

In [98]:
cursor = db['covid_comedy_youtube_transcripts2'].find()

In [73]:
#list(cursor)

In [79]:
# List all the book titles with the author
#cursor = db.author.find({}, {'_id':0, 'name': 1, 'books.title':1})

#list(cursor)

In [137]:
#db1 = db.covid_comedy_youtube_comments.aggregate([{ '$unwind': '$items' }])
#db.inventory.aggregate( [ { $unwind : "$sizes" } ] )

In [140]:
#list(db1)

In [99]:
cursor = db.covid_comedy_youtube_transcripts2.find({}, {'_id':0, 'url': 1, 
                                                    'transcript.text':1})

In [100]:
df =  pd.DataFrame(list(cursor))

In [101]:
df = df.dropna()#.astype(str)#replace("{'text': ", '')

In [102]:
df.head()

url                                         transcript
0  _5DXs8xxaMU  [{'text': 'yeah I really don't understand why'...
1  DNrMPF3I_bs  [{'text': '[Music]'}, {'text': 'it's the Unite...
3  TwN8soCzjPM  [{'text': 'testing one two I don't know if thi...
4  8OMUdYoIJhI  [{'text': 'hello again I'm Walter to continue ...
5  xk_MHfOAfRQ  [{'text': 'oh whoa who are you I'm Julie from ...

In [82]:
df.set_index('url', inplace=True)

In [107]:
with open('video_id_transcript_bulk_df_semi_clean.pkl', 'wb') as picklefile:
    pickle.dump(df, picklefile)

In [104]:
new_df = pd.concat([pd.DataFrame(','.join(pd.DataFrame(json_normalize(x)))) for x in df['transcript']]) #,ignore_index=True

ValueError: DataFrame constructor not properly called!

In [ ]:
.transform(lambda x: ','.join(x)

In [88]:
new_df

text
0         yeah I really don't understand why
1   everybody isn't following the same rules
2      right now they're very clear so let's
3     take a minute let's go over them again
4      first you must not leave that for any
..                                       ...
30                                   [Music]
31                                        Oh
32                                   [Music]
33                                   [Music]
34                                   [Music]

[41893 rows x 1 columns]

In [ ]:
##Junk

In [77]:
#df['transcript'][0]

In [ ]:
#toy_econ = toy_econ.drop(['labour_participation_gender_f_to_m_perc_b'], axis=1)

In [59]:
type(df['transcript'])

pandas.core.series.Series

In [60]:
# Text preprocessing steps - remove numbers, captial letters and punctuation
import re
import string

alphanumeric = lambda x: re.sub('\w*\d\w*', ' ', x)
punc_lower = lambda x: re.sub('[%s]' % re.escape(string.punctuation), ' ', x.lower())

#df['transcript'] = df['transcript'].map(alphanumeric).map(punc_lower)
#df.head()

In [67]:
str(df['transcript'][0]).replace("'text': ", "")

'[{"yeah I really don\'t understand why"}, {"everybody isn\'t following the same rules"}, {"right now they\'re very clear so let\'s"}, {"take a minute let\'s go over them again"}, {\'first you must not leave that for any\'}, {\'reason unless of course you have a\'}, {\'reason and then you may leave the house\'}, {\'all stores are closed except those that\'}, {\'are open in all stores must closed\'}, {\'unless of course they need to stay open\'}, {"this virus is deadly but don\'t be afraid"}, {\'of it it can only kill people who are\'}, {\'vulnerable and also those who are not\'}, {\'vulnerable\'}, {\'we should stay lockdown until the virus\'}, {\'stops infecting people and it will only\'}, {\'stop infecting people if enough of us\'}, {\'get infected that we build immunity so\'}, {\'it is very important that we get\'}, {\'infected and also do not get infected\'}, {"you should not go to the doctor\'s office"}, {\'or the hospital unless you have to go\'}, {\'there unless of course you are

In [54]:
pd.concat([df, json_normalize(df['transcript'])])

AttributeError: 'list' object has no attribute 'values'

In [43]:
new_df = pd.concat([pd.DataFrame(json_normalize(x)) for x in df['transcript']]) #,ignore_index=True

In [46]:
new_df

text
0         yeah I really don't understand why
1   everybody isn't following the same rules
2      right now they're very clear so let's
3     take a minute let's go over them again
4      first you must not leave that for any
..                                       ...
30                                   [Music]
31                                        Oh
32                                   [Music]
33                                   [Music]
34                                   [Music]

[41893 rows x 1 columns]

In [175]:
new_df_text = pd.DataFrame(new_df.groupby(['snippet.videoId','snippet.topLevelComment.snippet.likeCount'] )['snippet.topLevelComment.snippet.textDisplay'].apply(lambda x: "{%s}" % ', '.join(x)))

In [45]:
pd.concat([df, new_df_text], axis=1)

NameError: name 'new_df_text' is not defined

In [176]:
new_df_text

snippet.topLevelComment.snippet.textDisplay
snippet.videoId snippet.topLevelComment.snippet.likeCount                                                   
-6Li2qT0ZkI     0                                          {Greetings from UK.. I love your videos ! Your...
                2                                          {I am covered under the blood of Jesus please ...
-CCW4Xnp_sQ     0                                          {Same problem over here Randy, only with less ...
                1                                          {You are so LOVED and right on point! 😘😘😘😘😘, B...
-Cg1jBuYZYM     0                                                                {😄😄😄😄😄, Ahahahah, Bhut shi}
...                                                                                                      ...
zTMlWzMe-h8     3                                          {<a href="https://www.youtube.com/watch?v=zTMl...
                6                                                            {If this man laughed at you...}
                11                                                  {Laughing to death, His laugh kills me.}
zqOMkTvqaDY     0                                          {...they laughed maniacally as they pulled awa...
zqolMo_nv5U     0                                                     {Nice Comedy Shekinah, Nice one, 🤯👍🤯🤯}

[1332 rows x 1 columns]

In [ ]:
new_df_text.t

In [173]:
import pickle
with open('video_id_comments_bulk_df.pkl', 'wb') as picklefile:
    pickle.dump(new_df_text, picklefile)

In [ ]:
####

In [90]:
import pandas as pd
from bson import json_util, ObjectId
from pandas.io.json import json_normalize
import json

def mongo_to_dataframe(mongo_data):

        sanitized = json.loads(json_util.dumps(mongo_data))
        normalized = json_normalize(sanitized)
        df = pd.DataFrame(normalized)

        return df

In [ ]:
#sanitized = json.loads(json_util.dumps(collection.find({},{"id": 1, "text": 1, "user.id": 1}))) 

In [129]:
data = mongo_to_dataframe(cursor)
data.head()

Empty DataFrame
Columns: []
Index: []

In [111]:
sanitized = json.loads(json_util.dumps(db.covid_comedy_youtube_comments.find({},{"_id": 1, "etag": 1, "items.snippet": 1}))) 


In [112]:
#sanitized = json.loads(json_util.dumps(list(cursor)))
sanitized

[{'_id': {'$oid': '5eb9d934bf302180d66eab96'},
  'etag': 'LqNtsL6AXCjJcM7lV0VFuTDNPXo',
  'items': [{'snippet': {'videoId': '_5DXs8xxaMU',
     'topLevelComment': {'kind': 'youtube#comment',
      'etag': 'zJCFlnvcMmUtJe4gHWmJNHfgFzs',
      'id': 'UgxjZ-RWhzzRPiCzmJB4AaABAg',
      'snippet': {'videoId': '_5DXs8xxaMU',
       'textDisplay': 'She has like 32k likes on on another link.  She also got 1 million views. Or 2 million or 3 million or plastic in the air.',
       'textOriginal': 'She has like 32k likes on on another link.  She also got 1 million views. Or 2 million or 3 million or plastic in the air.',
       'authorDisplayName': 'Benedetto Sorrentino II',
       'authorProfileImageUrl': 'https://yt3.ggpht.com/a/AATXAJybfZMI_e3n4PfefSveqY0hfBBR4gNKe6G_xw=s48-c-k-c0xffffffff-no-rj-mo',
       'authorChannelUrl': 'http://www.youtube.com/channel/UCxuLY-6UjdKp1HGBG-QGHhg',
       'authorChannelId': {'value': 'UCxuLY-6UjdKp1HGBG-QGHhg'},
       'canRate': True,
       'viewerRating

In [113]:
normalized = json_normalize(sanitized)

In [114]:
normalized
df = pd.DataFrame(normalized)

In [115]:
df['items']

0      [{'snippet': {'videoId': '_5DXs8xxaMU', 'topLe...
1      [{'snippet': {'videoId': 'DNrMPF3I_bs', 'topLe...
2      [{'snippet': {'videoId': 'deNaIeeOGtA', 'topLe...
3      [{'snippet': {'videoId': 'TwN8soCzjPM', 'topLe...
4      [{'snippet': {'videoId': '8OMUdYoIJhI', 'topLe...
                             ...                        
616    [{'snippet': {'videoId': 'AS6cUYyA_qI', 'topLe...
617    [{'snippet': {'videoId': 'PdWiBR7hXj0', 'topLe...
618    [{'snippet': {'videoId': 'nrSTrK_bV7Y', 'topLe...
619                                                   []
620                                                   []
Name: items, Length: 621, dtype: object

In [116]:
def original(df):
    parsed_df = pd.concat([json_normalize(json.loads(js)) for js in df['items']])

    parsed_df['videoId'] = df['videoId'].values
    parsed_df.index = parsed_df['uid']

    return parsed_df

In [121]:
df['items'] = df['items'].astype(str)

In [126]:
df['items']

0      [{'snippet': {'videoId': '_5DXs8xxaMU', 'topLe...
1      [{'snippet': {'videoId': 'DNrMPF3I_bs', 'topLe...
2      [{'snippet': {'videoId': 'deNaIeeOGtA', 'topLe...
3      [{'snippet': {'videoId': 'TwN8soCzjPM', 'topLe...
4      [{'snippet': {'videoId': '8OMUdYoIJhI', 'topLe...
                             ...                        
616    [{'snippet': {'videoId': 'AS6cUYyA_qI', 'topLe...
617    [{'snippet': {'videoId': 'PdWiBR7hXj0', 'topLe...
618    [{'snippet': {'videoId': 'nrSTrK_bV7Y', 'topLe...
619                                                   []
620                                                   []
Name: items, Length: 621, dtype: object

In [127]:
df['items'].replace("snippet", '')#.replace("]", '')

0      [{'snippet': {'videoId': '_5DXs8xxaMU', 'topLe...
1      [{'snippet': {'videoId': 'DNrMPF3I_bs', 'topLe...
2      [{'snippet': {'videoId': 'deNaIeeOGtA', 'topLe...
3      [{'snippet': {'videoId': 'TwN8soCzjPM', 'topLe...
4      [{'snippet': {'videoId': '8OMUdYoIJhI', 'topLe...
                             ...                        
616    [{'snippet': {'videoId': 'AS6cUYyA_qI', 'topLe...
617    [{'snippet': {'videoId': 'PdWiBR7hXj0', 'topLe...
618    [{'snippet': {'videoId': 'nrSTrK_bV7Y', 'topLe...
619                                                   []
620                                                   []
Name: items, Length: 621, dtype: object

In [128]:
pd.concat([df, json_normalize(df['items'])])

AttributeError: 'str' object has no attribute 'values'

In [122]:
import json
from pandas.io.json import json_normalize

parsed_df = pd.concat([json_normalize(json.loads(js)) for js in df['items']])



JSONDecodeError: Expecting property name enclosed in double quotes: line 1 column 3 (char 2)

In [94]:

#df = pandas.DataFrame(t)
df['items.snippet'] = df['items'].apply(lambda cell: cell['snippet'])
df['items'] = df['items'].apply(lambda cell: dict((k, v) for k, v in cell))

TypeError: list indices must be integers or slices, not str

In [ ]:
df['stage.name'] = df['stage'].apply(lambda cell: cell['Name'])
df['q_']= df['quality'].apply(lambda cell: [(m['type']['Name'], m['value'] if 'value' in m.keys() else 1) for m in cell])
df['q_'] = df['q_'].apply(lambda cell: dict((k, v) for k, v in cell))
keys = set(chain(*df['q_'].apply(lambda column: column.keys())))
for key in keys:
    column_name = 'q_{}'.format(key).lower()
    df[column_name] = df['q_'].apply(lambda cell: cell[key] if key in cell.keys() else numpy.NaN) 
df.drop(['stage', 'quality', 'q_'], axis=1, inplace=True)